In [1]:
import pandas as pd
from ch2.data import *
from ch2.squeal.database import connect

s = session('-v 0')
raw = activity_statistics(s, SPEED, DISTANCE, ELEVATION, CADENCE, LATITUDE, LONGITUDE, HEART_RATE,
                         local_time='2018-03-04 12:00', activity_group_name='Bike', with_timespan=True)
raw.describe()

Latitude    Longitude        Speed       Distance      Cadence  \
count  2885.000000  2885.000000  2886.000000    2933.000000  2903.000000   
mean    -33.473723   -70.806271     5.694779   52424.331323    61.558043   
std       0.034321     0.108272     2.914509   29499.017849    45.063903   
min     -33.549516   -70.949936     0.000000       0.000000     0.000000   
25%     -33.501597   -70.922318     3.154000   29534.110000     0.000000   
50%     -33.460546   -70.826145     6.196000   52038.000000    87.000000   
75%     -33.448303   -70.706109     7.539000   79518.980000   100.000000   
max     -33.420239   -70.607797    13.175000  102708.060000   159.000000   

        Heart Rate    Elevation   Timespan ID  
count  2933.000000  2784.000000   2832.000000  
mean    114.568360   580.671118  19441.079802  
std      13.942284   149.218650     31.450027  
min      65.000000   401.366177  19348.000000  
25%     105.000000   479.115404  19414.000000  
50%     115.000000   518.720135  19435.000000  
75%     125.000000   617.829422  19462.250000  
max     161.000000   997.497194  19500.000000

In [2]:
from ch2.data.power import *

df = linear_resample(raw)
df = add_differentials(df)
df = add_energy_budget(df, m=64+12)
df = add_air_speed(df, 0, 0)
df = add_loss_estimate(df)
df = add_power_estimate(df)
print(measure_initial_scaling(df))
df = add_modeled_hr(df, 3600, 0.16, 15)


(0.08786694407125391, 110.29083252672575, 14.0)


In [3]:
model = fit_power(df, PowerModel(cda=0.45, slope=0.08, delay=14), 
                  'slope', 'delay')
print(model)

PowerModel(cda=0.45, crr=0, slope=0.01468373335429441, window=3600, delay=11.345171328628341, m=70, wind_speed=0, wind_heading=0)


In [4]:
df = add_modeled_hr(df, 3600, 0.177, 15)

In [5]:
from bokeh.plotting import output_notebook, show
from bokeh.layouts import row, column

from ch2.data.plot import *

output_notebook()
df['error'] = df[DETRENDED_HEART_RATE] - df[PREDICTED_HEART_RATE]
show(column([comparison_line_plot(700, 200, TIME, y, df) 
             for y in (POWER, HEART_RATE, DETRENDED_HEART_RATE, PREDICTED_HEART_RATE, 'error')]))


Loading BokehJS ...

In [6]:
print(1800 / median_dt(df))
df[HEART_RATE].rolling(360, center=True, min_periods=1).median()

257.14285714285717


2018-03-04 10:16:33+00:00    101.000000
2018-03-04 10:16:40+00:00    101.000000
2018-03-04 10:16:47+00:00    101.000000
2018-03-04 10:16:54+00:00    101.000000
2018-03-04 10:17:01+00:00    101.000000
2018-03-04 10:17:08+00:00    101.125000
2018-03-04 10:17:15+00:00    101.250000
2018-03-04 10:17:22+00:00    101.339286
2018-03-04 10:17:29+00:00    101.428571
2018-03-04 10:17:36+00:00    101.464286
2018-03-04 10:17:43+00:00    101.500000
2018-03-04 10:17:50+00:00    101.583333
2018-03-04 10:17:57+00:00    101.666667
2018-03-04 10:18:04+00:00    101.666667
2018-03-04 10:18:11+00:00    101.666667
2018-03-04 10:18:18+00:00    101.666667
2018-03-04 10:18:25+00:00    101.666667
2018-03-04 10:18:32+00:00    101.722222
2018-03-04 10:18:39+00:00    101.777778
2018-03-04 10:18:46+00:00    101.888889
2018-03-04 10:18:53+00:00    102.000000
2018-03-04 10:19:00+00:00    102.000000
2018-03-04 10:19:07+00:00    102.000000
2018-03-04 10:19:14+00:00    102.000000
2018-03-04 10:19:21+00:00    102.000000
